In [1]:
import numpy as np
import matplotlib.pyplot as plt
import time
import csv
from scipy import optimize

In [2]:
# nearest-neighbor interaction
def interaction(phase):
    return K*(np.sin(np.roll(phase,1,axis=0) - phase) 
            + np.sin(np.roll(phase,-1,axis=0) - phase) 
            + np.sin(np.roll(phase,1,axis=1) - phase)
            + np.sin(np.roll(phase,-1,axis=1) - phase))

In [7]:
Lx = 1000 # system size = Lx x Ly
Ly = 20
T = 0.002 # temperature
sigma = 0.005
K = 4 # strength of interaction
kmax = 5 # total number of Fourier components

num_of_samples = 100 # number of samples
n_steps = int(1e5) # simulation steps
dt = 0.001 # time increment
t_run = n_steps * dt # simulation time
intvl = 1

In [8]:
start_time = time.time()

# auxiliary array to calculate Fourier modes (x-direction)
aux = np.divmod(np.arange(Lx*Ly).reshape((Lx,Ly)),Ly)[0]

for s in range(num_of_samples):
    phase = np.zeros((Lx,Ly)) # phase of oscillators
    frequency = np.random.normal(0,sigma,(Lx,Ly)) # intrinsic freqency (Gaussian)
    psi = np.zeros(n_steps,dtype=complex) # order parameter
    modes = np.zeros(kmax,dtype=complex) # Fourier modes (k = 0, 2pi/L, 4pi/L, ..., k_max)
    
    # initialization of phase of oscillators (left 1/2: 0, right 1/2: pi/2)
    phase[:int(Lx/10),:] = np.full((int(Lx/10),Ly),np.pi/2)
    phase[int(Lx/10):,:] = np.full((Lx-int(Lx/10),Ly),0)
    psi = np.average(np.exp(1j*phase[:,:]))

    # relaxation
    with open('./Kuramoto_model_relaxation/Lx%d_Ly%d_K%d_T%.1e_sigma%.1e_dt%.1e_t%.1e_S%d.csv'%(Lx,Ly,K,T,sigma,dt,t_run,s), 'w', newline='') as file:
        writer = csv.writer(file)
        #writer.writerow(["time","order parameter", "phase"])

        for t in range(n_steps-1):
            noise = np.random.normal(0,np.sqrt(2*T*dt),(Lx,Ly))
            phase_tmp = phase + ( frequency + interaction(phase) ) * dt + noise
            phase_diff = ( frequency + (interaction(phase) + interaction(phase_tmp))/2 ) * dt + noise
            phase += phase_diff

            if t%intvl == 0:
                psi = np.average(np.exp(1j*phase[:,:]))
                psi_angle = np.angle(psi)
                phi = np.angle(np.exp(1j*phase) * np.exp(-1j*psi_angle))
                for k in range(kmax):
                    modes[k] = np.sum(phi * np.exp(2j*np.pi*aux*(k+1)/Lx))
                writer.writerow([t*dt,psi,modes[0],modes[1],modes[2],modes[3],modes[4]])
        
print("--- %s seconds ---" % (time.time() - start_time))

--- 56836.684415102005 seconds ---
